This notebook can be executed on either cpu or gpu runtime.

To run on gpu, change the
```
.to('cpu')
```
to

```
.to('gpu')
```

In [9]:
# Download nessecary libraries
!pip install datasets==2.10.0 --quiet
!pip install transformers --quiet

In [10]:
from google.colab import drive
drive.mount('/content/drive/')
root_dir = "./drive/MyDrive/ASR_Colab/" #change it to your own path

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [11]:
# Load the preprocessed dataet
from datasets import load_from_disk
from os import path
import numpy as np

ds_test = load_from_disk(path.join(root_dir , "dataset.hf/test"))

In [12]:
from transformers import  Wav2Vec2CTCTokenizer ,Wav2Vec2FeatureExtractor,Wav2Vec2Processor

tokenizer = Wav2Vec2CTCTokenizer(path.join(root_dir ,"vocab.json"), unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")
feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)
processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [15]:
# Load the model weights
from transformers import Wav2Vec2ForCTC
model = Wav2Vec2ForCTC.from_pretrained(path.join(root_dir ,"model_weights")).to("cpu")

In [16]:
# select 20 random samples from the test dataset
selected_samples = np.random.randint(low = 0 , high= len(ds_test) , size=20)

In [17]:
import torch

# Initialize empty lists to store predicted outputs and other columns
predicted = []
real_sentences = []
audios = []
gender = []
accent = []
tone = []


# Iterate through the selected samples in the test dataset
for sample in ds_test.select(selected_samples):
  model_input = processor(sample["input_values"], return_tensors="pt", padding=True,sampling_rate=16000)

  # Move the input values to GPU and obtain model predictions
  logits = model(model_input.input_values.to("cpu")).logits
  pred_ids = torch.argmax(logits, dim=-1)[0]

  # Append the predicted output, real sentence labels, and audio inputs and other columns to their respective lists
  predicted.append(pred_ids)
  real_sentences.append(sample["transcript"])
  audios.append(sample["input_values"])
  gender.append(sample["gender"])
  accent.append(sample["accent"])
  tone.append(sample["tone"])

In [18]:
import IPython.display as ipd

dashed = "_-_-"*100

for id_sample in range(len(predicted)):
  # Display the predicted text generated by the model
  print("Prediction:")
  print(processor.decode(predicted[id_sample]))

  # Display the reference (real) text
  print("\nReference:")
  print(real_sentences[id_sample])

  # Display the audio
  print("\nAudio:")
  speech = audios[id_sample]

  # Display the audio using IPython Audio with autoplay enabled
  ipd.display(ipd.Audio(data=speech, rate=16000))

  print(f'gender: {gender[id_sample]}, accent: {accent[id_sample]}, tone: {tone[id_sample]}')
  print(dashed)

Prediction:
در هریرت دمباله از سفویک را زخیده کرده

Reference:
در حقیقت دنباله ای از صفر و یک را ذخیره کرده ایم. 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
او در بسیر سر آیتهالی کلاسیش ورجت میکند

Reference:
او در بسیاری از فعالیتهای کلاسی شرکت میکند. 

Audio:


gender: male , accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
ما ب هیچ و اچ نمی توانیم در مقابل این تهولات مقاومد کنیم

Reference:
ما به هیچ وجه نمی توانیم در مقابل این تحولات مقاومت کنیم. 

Audio:


gender: male, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
م خق شده ایم تازجر به کشیم و همه این را میدانیم ولی سی می کنیم و سایلی اخت را کنیم تا خود مان را گول بزنی

Reference:
ما خلق شده ایم تا زجر بکشیم و همه این را می دانیم ولی سعی می کنیم وسایلی اختراع کنیم تا خودمان را گول بزنیم. 

Audio:


gender: female, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
آیا میخواهید در این ج گرفبازی کنید

Reference:
آیا می خواهید در اینچا گلف بازی کنید؟ 

Audio:


...

gender: female, accent: فارسی, tone: question
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
چن درس از بارش سالانه باران دریران در سماه زمستان رخ میتهد

Reference:
چند درصد از بارش سالانه باران در ایران در سه ماه زمستان رخ می دهد؟ 

Audio:


gender: male, accent: فارسی, tone: question
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
لوبیا قرمز را یکی دو دقیق تفتهید سفس لیو ان آب به قابلمه ازاف کنید.

Reference:
لوبیا قرمز را یکی دو دقیقه تفت دهید سپس سه لیوان آب به قابلمه اضافه کنید. 

Audio:


gender: مرد, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
برخی این های نوروز در این کشور ها به متفاوتن براینه در افخانستام سفره هفت به میچینند امادر یرن سفره هفتی میندازند

Reference:
امروزه پرتونگاری بسیار مورد توجه دانشمندان قرار گرفته است چرا که تصاویر با دقت بالا را ارائه می دهند. 

Audio:


gender: female, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
Prediction:
موجزه برای کسانی تفاق میفتد که به آن اتقاد دارند

Reference:
معجزه برای کسانی اتفاق می افتد که به آن اعتقاد دارند . 

Audio:


gender: female, accent: فارسی, tone: normal
_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-_-
